Generate chord diagrams to look at interactions between clones in tumours

We use holoviews with a matplotlib backend. 

Initial part of the code runs through how to prepare the data for generating the graphs.

In [ ]:
import pandas as pd 
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from itertools import combinations
from collections import Counter

#print software versions

print("Pandas version: ", pd.__version__)
print("Seaborn version: ", sns.__version__)
print("Matplotlib version: ", plt.matplotlib.__version__)
print("Numpy version: ", np.__version__)

import sys
print("Python version: ", sys.version)


merged_df = pd.read_csv("./MFP_IV_combined_raw_data.csv")
 

#define a function to get get radius given volume 
def get_radius(volume):
    return (3*volume/(4*np.pi))**(1/3)

#add a column for radius
merged_df['radius_met'] = merged_df['Volume corrected'].apply(get_radius)
#normalized min distance to radius_met
merged_df['min_dist_norm'] = merged_df['min_dist'] / merged_df['radius_met']
merged_df.head()

Pandas version:  2.2.1
Seaborn version:  0.13.2
Matplotlib version:  3.8.4
Numpy version:  1.23.4
Python version:  3.10.14 | packaged by Anaconda, Inc. | (main, Mar 21 2024, 16:20:14) [MSC v.1916 64 bit (AMD64)]


C:\Users\rajasekhar.p\AppData\Local\Temp\ipykernel_43372\3372598194.py:20: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  merged_df = pd.read_csv("./MFP_IV_combined_raw_data.csv")


MET_ID         1        10   11       100       101       110  111  \
0    28.0  0.011735  0.167993  0.0  0.511050  0.000000  0.309223  0.0   
1    50.0  0.998808  0.001192  0.0  0.000000  0.000000  0.000000  0.0   
2    89.0  0.175399  0.099498  0.0  0.545721  0.179381  0.000000  0.0   
3   119.0  0.974494  0.001366  0.0  0.024140  0.000000  0.000000  0.0   
4   125.0  0.975769  0.000219  0.0  0.024012  0.000000  0.000000  0.0   

   Volume corrected    min_dist  ...  treatment  total_lung_volume  \
0      2.202260e+08    0.000000  ...         IV       2.775850e+10   
1      6.563523e+04  282.432010  ...         IV       2.775850e+10   
2      1.246517e+08   15.761827  ...         IV       2.775850e+10   
3      1.326004e+06    0.000000  ...         IV       2.775850e+10   
4      1.016321e+07    0.000000  ...         IV       2.775850e+10   

   vessel_volume  vessel_surface_area  minor_axis  major_axis  elongation  \
0   8.529756e+08         1.510170e+08  161.040177  337.000000    2.092645   
1   8.529756e+08         1.510170e+08   13.000000   18.336258    1.410481   
2   8.529756e+08         1.510170e+08  167.418006  376.000000    2.245876   
3   8.529756e+08         1.510170e+08   37.469744   55.000000    1.467851   
4   8.529756e+08         1.510170e+08   76.533946  111.000000    1.450337   

   met_type_cat  radius_met  min_dist_norm  
0    polyclonal  374.622027       0.000000  
1    polyclonal   25.023581      11.286634  
2    polyclonal  309.886884       0.050863  
3    polyclonal   68.153062       0.000000  
4    polyclonal  134.373652       0.000000  

[5 rows x 46 columns]

To generate chord diagrams, we need to get all possible combinations of interactions between MET clones

So, if a met has [1,4,5] clones, then all possible combinations are [1,4], [1,5] and [4,5].. 

If we have [1,4,5] and [4,5,6], then all possible combinations are [1,4], [1,5], [4,5], [4,5], [5,6], [4,6]. 

If we count number of interactions:
- `[1,4]: 1`
- `[1,5]: 1  `
- `[4,5]: 2  `
- `[5,6]: 1  `
- `[4,6]: 1`

This information is used to generate a graph for the chord diagram

## Polyclonal only

Get polyclonal Mets only for chord graph, as only polyclonal have multiple METs

In [3]:
poly_only = merged_df[merged_df['met_type_cat'] == 'polyclonal']
clone_type_df = poly_only[['clone_type']].astype(str)
clone_type_df.head()

clone_type
0    1_2_4_6
1        1_2
2    1_2_4_5
3      1_2_4
4      1_2_4

Create a column 'clone_list' where the clone_type is converted into a list of clone numbers, so 1_4_5 becomes [1,4,5]

In [4]:
#split rows with "_" and if it doesn't have _, then add value in clone_type column
clone_type_df['clone_list'] = clone_type_df['clone_type'].apply(lambda x: x.split('_') if '_' in x else [x])
clone_type_df.head()

clone_type    clone_list
0    1_2_4_6  [1, 2, 4, 6]
1        1_2        [1, 2]
2    1_2_4_5  [1, 2, 4, 5]
3      1_2_4     [1, 2, 4]
4      1_2_4     [1, 2, 4]

For each row, we get all get all possible combinations of pairs in that row. 

So, if a met has [1,4,5] clones, then all possible combinations are [1,4], [1,5] and [4,5].. 

The Counter function will count the number of occurences of each pair in all of the data

In [5]:
#For each row, get all possible combinations of pairs
all_pairs = [tuple(sorted(pair)) for sublist in clone_type_df['clone_list'] for pair in combinations(sublist, 2)]
comb_counter = Counter(all_pairs)
comb_counter

Counter({('1', '4'): 964,
         ('1', '2'): 434,
         ('2', '4'): 383,
         ('1', '3'): 134,
         ('3', '4'): 102,
         ('2', '3'): 73,
         ('1', '6'): 63,
         ('4', '6'): 62,
         ('4', '5'): 62,
         ('1', '5'): 60,
         ('1', '7'): 57,
         ('4', '7'): 56,
         ('2', '6'): 41,
         ('2', '7'): 36,
         ('2', '5'): 25,
         ('3', '7'): 17,
         ('3', '6'): 15,
         ('6', '7'): 15,
         ('5', '7'): 6,
         ('5', '6'): 6,
         ('3', '5'): 6})

In [6]:
#save combinations to a dataframe
comb_df = pd.DataFrame.from_dict(comb_counter, orient='index').reset_index()
comb_df.columns = ['pair', 'count']
import os 
#create a dir fig4 in final_graphs
os.makedirs("./final_graphs/fig4", exist_ok=True)
comb_df.to_csv("./final_graphs/fig4/pair_combinations_combined.csv", index=False)

Convert the above to a dataframe and make sure count column is at the end

In [7]:
connections = pd.DataFrame(comb_counter.items(), columns=['pair', 'count'])
connections[['clone_a', 'clone_b']] = pd.DataFrame(connections['pair'].tolist(), index=connections.index)
connections.drop(columns=['pair'], inplace=True)
connections = connections.astype(int)
#put the Count column at the end
connections = connections[['clone_a', 'clone_b', 'count']]
connections.head()

clone_a  clone_b  count
0        1        2    434
1        1        4    964
2        1        6     63
3        2        4    383
4        2        6     41

We use holoviews with a matplotlib backend for generating the chord diagram

In [11]:
import holoviews as hv
import matplotlib.colors as mcolors
print("Holoviews version: ", hv.__version__)
hv.extension('matplotlib')
hv.output(fig='svg', size=250)

Holoviews version:  1.20.2


<img src='data:image/png;base64,iVBORw0KGgoAAAANSUhEUgAAAEAAAABACAYAAACqaXHeAAAABHNCSVQICAgIfAhkiAAAAAlwSFlz
AAAB+wAAAfsBxc2miwAAABl0RVh0U29mdHdhcmUAd3d3Lmlua3NjYXBlLm9yZ5vuPBoAAA6zSURB
VHic7ZtpeFRVmsf/5966taWqUlUJ2UioBBJiIBAwCZtog9IOgjqACsogKtqirT2ttt069nQ/zDzt
tI4+CrJIREFaFgWhBXpUNhHZQoKBkIUASchWla1S+3ar7r1nPkDaCAnZKoQP/D7mnPOe9/xy76n3
nFSAW9ziFoPFNED2LLK5wcyBDObkb8ZkxuaoSYlI6ZcOKq1eWFdedqNzGHQBk9RMEwFAASkk0Xw3
ETacDNi2vtvc7L0ROdw0AjoSotQVkKSvHQz/wRO1lScGModBFbDMaNRN1A4tUBCS3lk7BWhQkgpD
lG4852/+7DWr1R3uHAZVQDsbh6ZPN7CyxUrCzJMRouusj0ipRwD2uKm0Zn5d2dFwzX1TCGhnmdGo
G62Nna+isiUqhkzuKrkQaJlPEv5mFl2fvGg2t/VnzkEV8F5ioioOEWkLG86fvbpthynjdhXYZziQ
x1hC9J2NFyi8vCTt91Fh04KGip0AaG9zuCk2wQCVyoNU3Hjezee9bq92duzzTmxsRJoy+jEZZZYo
GTKJ6SJngdJqAfRzpze0+jHreUtPc7gpBLQnIYK6BYp/uGhw9YK688eu7v95ysgshcg9qSLMo3JC
4jqLKQFBgdKDPoQ+Pltb8dUyQLpeDjeVgI6EgLIQFT5tEl3rn2losHVsexbZ3EyT9wE1uGdkIPcy
BGxn8QUq1QrA5nqW5i2tLqvrrM9NK6AdkVIvL9E9bZL/oyfMVd/jqvc8LylzRBKDJSzIExwhQzuL
QYGQj4rHfFTc8mUdu3E7yoLtbTe9gI4EqVgVkug2i5+uXGo919ixbRog+3fTbQ8qJe4ZOYNfMoTI
OoshUNosgO60AisX15aeI2PSIp5KiFLI9ubb1vV3Qb2ltwLakUCDAkWX7/nHKRmmGIl9VgYsUhJm
2NXjKYADtM1ygne9QQDIXlk49FBstMKx66D1v4+XuQr7vqTe0VcBHQlRWiOCbmmSYe2SqtL6q5rJ
zsTb7lKx3FKOYC4DoqyS/B5bvLPxvD9Qtf6saxYLQGJErmDOdOMr/zo96km1nElr8bmPOBwI9COv
HnFPRIwmkSOv9kcAS4heRsidOkpeWBgZM+UBrTFAXNYL5Vf2ii9c1trNzpYdaoVil3WIc+wdk+gQ
noie3ecCcxt9ITcLAPWt/laGEO/9U6PmzZkenTtsSMQ8uYywJVW+grCstAvCIaAdArAsIWkRDDs/
KzLm2YcjY1Lv0UdW73HabE9n6V66cxSzfEmuJssTpKGVp+0vHq73FwL46eOjpMpbRAnNmJFrGJNu
Ukf9Yrz+3rghiumCKNXXWPhLYcjxGsIpoCMsIRoFITkW8AuyM8jC1+/QLx4bozCEJIq38+1rtpR6
V/yzb8eBlRb3fo5l783N0CWolAzJHaVNzkrTzlEp2bQ2q3TC5gn6wpnoQAmwSiGh2GitnTmVMc5O
UyfKWUKCIsU7+fZDKwqdT6DDpvkzAX4/+AMFjk0tDp5GRXLpQ2MUmhgDp5gxQT8+Y7hyPsMi8uxF
71H0oebujHALECjFKaW9Lm68n18wXp2kVzIcABytD5iXFzg+WVXkegpAsOOYziqo0OkK76GyquC3
ltZAzMhhqlSNmmWTE5T6e3IN05ITFLM4GdN0vtZ3ob8Jh1NAKXFbm5PtLU/eqTSlGjkNAJjdgn/N
aedXa0tdi7+t9G0FIF49rtMSEgAs1kDLkTPO7ebm4IUWeyh1bKomXqlgMG6kJmHcSM0clYLJ8XtR
1GTnbV3F6I5wCGikAb402npp1h1s7LQUZZSMIfALFOuL3UUrfnS8+rez7v9qcold5tilgHbO1fjK
9ubb17u9oshxzMiUBKXWqJNxd+fqb0tLVs4lILFnK71H0Ind7uiPgACVcFJlrb0tV6DzxqqTIhUM
CwDf1/rrVhTa33/3pGPxJYdQ2l2cbgVcQSosdx8uqnDtbGjh9SlDVSMNWhlnilfqZk42Th2ZpLpf
xrHec5e815zrr0dfBZSwzkZfqsv+1FS1KUknUwPARVvItfKUY+cn57yP7qv07UE3p8B2uhUwLk09
e0SCOrK+hbdYHYLjRIl71wWzv9jpEoeOHhGRrJAzyEyNiJuUqX0g2sBN5kGK6y2Blp5M3lsB9Qh4
y2Ja6x6+i0ucmKgwMATwhSjdUu49tKrQ/pvN5d53ml2CGwCmJipmKjgmyuaXzNeL2a0AkQ01Th5j
2DktO3Jyk8f9vcOBQHV94OK+fPumJmvQHxJoWkaKWq9Vs+yUsbq0zGT1I4RgeH2b5wef7+c7bl8F
eKgoHVVZa8ZPEORzR6sT1BzDUAD/d9F78e2Tzv99v8D+fLVTqAKAsbGamKey1Mt9Ann4eH3gTXTz
idWtAJ8PQWOk7NzSeQn/OTHDuEikVF1R4z8BQCy+6D1aWRfY0tTGG2OM8rRoPaeIj5ZHzJxszElN
VM8K8JS5WOfv8mzRnQAKoEhmt8gyPM4lU9SmBK1MCQBnW4KONT86v1hZ1PbwSXPw4JWussVjtH9Y
NCoiL9UoH/6PSu8jFrfY2t36erQHXLIEakMi1SydmzB31h3GGXFDFNPaK8Rme9B79Ixrd0WN+1ij
NRQ/doRmuFLBkHSTOm5GruG+pFjFdAmorG4IXH1Qua6ASniclfFtDYt+oUjKipPrCQB7QBQ2lrgP
fFzm+9XWUtcqJ3/5vDLDpJ79XHZk3u8nGZ42qlj1+ydtbxysCezrydp6ugmipNJ7WBPB5tydY0jP
HaVNzs3QzeE4ZpTbI+ZbnSFPbVOw9vsfnVvqWnirPyCNGD08IlqtYkh2hjZ5dErEQzoNm+6ykyOt
Lt5/PQEuSRRKo22VkydK+vvS1XEKlhCJAnsqvcVvH7f/ZU2R67eXbMEGAMiIV5oWZWiWvz5Fv2xG
sjqNJQRvn3Rs2lji/lNP19VjAQDgD7FHhujZB9OGqYxRkZxixgRDVlqS6uEOFaJUVu0rPFzctrnF
JqijImVp8dEKVWyUXDk92zAuMZ6bFwpBU1HrOw6AdhQgUooChb0+ItMbWJitSo5Ws3IAOGEOtL53
0vHZih9sC4vtofZ7Qu6523V/fmGcds1TY3V36pUsBwAbSlxnVh2xLfAD/IAIMDf7XYIkNmXfpp2l
18rkAJAy9HKFaIr/qULkeQQKy9zf1JgDB2uaeFNGijo5QsUyacNUUTOnGO42xSnv4oOwpDi1zYkc
efUc3I5Gk6PhyTuVKaOGyLUAYPGIoY9Pu/atL/L92+4q9wbflRJ2Trpm/jPjdBtfnqB/dIThcl8A
KG7hbRuKnb8qsQsVvVlTrwQAQMUlf3kwJI24Z4JhPMtcfng5GcH49GsrxJpGvvHIaeem2ma+KSjQ
lIwUdYyCY8j4dE1KzijNnIP2llF2wcXNnsoapw9XxsgYAl6k+KzUXbi2yP3KR2ecf6z3BFsBICdW
nvnIaG3eHybqX7vbpEqUMT+9OL4Qpe8VON7dXuFd39v19FoAABRVePbGGuXTszO0P7tu6lghUonE
llRdrhArLvmKdh9u29jcFiRRkfLUxBiFNiqSU9icoZQHo5mYBI1MBgBH6wMNb+U7Pnw337H4gi1Y
ciWs+uks3Z9fztUvfzxTm9Ne8XXkvQLHNytOOZeiD4e0PgkAIAYCYknKUNUDSXEKzdWNpnil7r4p
xqkjTarZMtk/K8TQ6Qve78qqvXurGwIJqcOUKfUWHsm8KGvxSP68YudXq4pcj39X49uOK2X142O0
Tz5/u/7TVybqH0rSya6ZBwD21/gubbrgWdDgEOx9W

Using holoviews and matplotlib backend, create a chord diagram

In [12]:
#Using the connections df from above, create a Chord plot
hv.Chord(connections)


:Chord   [clone_a,clone_b]   (count)

Now, we need to add labels to the chord diagram

In [13]:
nodes = hv.Dataset(pd.DataFrame.from_records([
    {'index': 1, 'name': "1"},
    {'index': 2, 'name': "2"},
    {'index': 3, 'name': "3"},
    {'index': 4, 'name': "4"},
    {'index': 5, 'name': "5"},
    {'index': 6, 'name': "6"},
    {'index': 7, 'name': "7"}
]), 'index')

hv.Chord((connections, nodes)).opts(hv.opts.Chord(labels='name'))


:Chord   [clone_a,clone_b]   (count)

Lets add some colour to it better visualize the interactions between clone

In [ ]:

#Use a colourmap to for the nodes
color_map = ['cyan','yellow','lightgreen','magenta','purple','orange','lightgrey']
# Convert color names to hex values
hex_colors = [mcolors.to_hex(color) for color in color_map]

img = hv.Chord((connections, nodes)).opts(
    hv.opts.Chord(cmap=hex_colors, 
    edge_color=hv.dim('clone_a').astype(str),
    labels='name',
    node_color=hv.dim('index').astype(str),)
    #width=500,
    #height=500)
    )

img

#hv.save(img, './final_graphs/fig4/chord_diag_combined.svg', fmt='svg')


:Chord   [clone_a,clone_b]   (count)

Now we know how to generate a chord diagram with labels and colours, lets generate these for IV and MFP. 

We will also generate one for each animal

### Generate chord diagram for each treatment (IV and MFP)

Here we wrap the code from above into a `generate_connections` function for simplicity

In [14]:

hv.output(fig='svg', size=250)


def generate_connections(filtered_df):
    clone_type_df = filtered_df[['clone_type']].astype(str)
    #split rows with "_" and if it doesn't have _, then add value in clone_type column
    clone_type_df['clone_list'] = clone_type_df['clone_type'].apply(lambda x: x.split('_') if '_' in x else [x])
    #clone_type_df['clone_list'] = clone_type_df['clone_type'].str.split('_')
    all_pairs = [tuple(sorted(pair)) for sublist in clone_type_df['clone_list'] for pair in combinations(sublist, 2)]
    comb_counter = Counter(all_pairs)
    connections = pd.DataFrame(comb_counter.items(), columns=['pair', 'count'])
    connections[['clone_a', 'clone_b']] = pd.DataFrame(connections['pair'].tolist(), index=connections.index)
    connections.drop(columns=['pair'], inplace=True)
    connections = connections.astype(int)
    #put the Count column at the end
    connections = connections[['clone_a', 'clone_b', 'count']]
    connections.head()
    return connections,comb_counter

#generate nodes based on clone number
nodes = hv.Dataset(pd.DataFrame.from_records([
                                            {'index': 1, 'name': "1"},
                                            {'index': 2, 'name': "2"},
                                            {'index': 3, 'name': "3"},
                                            {'index': 4, 'name': "4"},
                                            {'index': 5, 'name': "5"},
                                            {'index': 6, 'name': "6"},
                                            {'index': 7, 'name': "7"}
                                        ]), 'index')

#Use a colourmap to for the nodes
color_map = ['cyan','yellow','lightgreen','magenta','purple','orange','lightgrey']
# Convert color names to hex values
hex_colors = [mcolors.to_hex(color) for color in color_map]

poly_only = merged_df[merged_df['met_type_cat'] == 'polyclonal']
clone_type_df_iv= poly_only[poly_only['treatment'] == 'IV'][['clone_type']]
clone_type_df_mfp = poly_only[poly_only['treatment'] == 'MFP'][['clone_type']]

connections_iv,iv_pairs  = generate_connections(clone_type_df_iv)
connections_mfp,mfp_pairs = generate_connections(clone_type_df_mfp)

#save combinations to a dataframe
iv_pairs_df = pd.DataFrame.from_dict(iv_pairs, orient='index').reset_index()
iv_pairs_df.columns = ['pair', 'count']
iv_pairs_df.to_csv("./final_graphs/fig4/IV_pair_combinations_combined.csv", index=False)

#mfp
mfp_pairs_df = pd.DataFrame.from_dict(mfp_pairs, orient='index').reset_index()
mfp_pairs_df.columns = ['pair', 'count']
mfp_pairs_df.to_csv("./final_graphs/fig4/MFP_pair_combinations_combined.csv", index=False)

In [15]:
chord_iv = hv.Chord((connections_iv, nodes)).opts(
    hv.opts.Chord(cmap=hex_colors, 
    edge_color=hv.dim('clone_a').astype(str),
    labels='name',
    node_color=hv.dim('index').astype(str),)
    )
chord_iv = chord_iv.relabel('Chord Diagram for IV')
hv.save(chord_iv, './final_graphs/fig4/chord_diag_IV.svg', fmt='svg')
chord_iv

:Chord   [clone_a,clone_b]   (count)

In [16]:
chord_mfp = hv.Chord((connections_mfp, nodes)).opts(
    hv.opts.Chord(cmap=hex_colors, 
    edge_color=hv.dim('clone_a').astype(str),
    labels='name',
    node_color=hv.dim('index').astype(str),)
    )
#add a title to the plot
chord_mfp = chord_mfp.relabel('Chord Diagram for MFP')
hv.save(chord_mfp, './final_graphs/fig4/chord_diag_MFP.svg', fmt='svg')
chord_mfp

:Chord   [clone_a,clone_b]   (count)

Generate a chord diagram for each animal

In [17]:
#Generate chord diagram for each mouse id 
ids = merged_df.id.unique()


chord_list = []

for id in ids:
    print(id)
    clone_type_df_id= poly_only[poly_only['id'] == id][['clone_type']]
    connections_id,id_pairs  = generate_connections(clone_type_df_id)
    #save combinations to a dataframe
    id_pairs_df = pd.DataFrame.from_dict(id_pairs, orient='index').reset_index()
    id_pairs_df.columns = ['pair', 'count']
    id_pairs_df.to_csv(f"final_graphs/fig4/{id}_pair_combinations_combined.csv", index=False)

    chord_id = hv.Chord((connections_id, nodes)).opts(
        hv.opts.Chord(cmap=hex_colors, 
        edge_color=hv.dim('clone_a').astype(str),
        labels='name',
        node_color=hv.dim('index').astype(str),)
        )
    chord_id = chord_id.relabel(f'Chord Diagram for {id}')
    #hv.save(chord_id, f'./final_graphs/fig4/chord_diag_{id}.svg', fmt='svg')
    
    chord_list.append(chord_id)


#Display chord diagram for each mouse id in one plot side by side
hv.Layout(chord_list).cols(3)


1064
1066
1067
1069
1070
1381
883
934
935


:Layout
   .Chord.Chord_Diagram_for_1064 :Chord   [clone_a,clone_b]   (count)
   .Chord.Chord_Diagram_for_1066 :Chord   [clone_a,clone_b]   (count)
   .Chord.Chord_Diagram_for_1067 :Chord   [clone_a,clone_b]   (count)
   .Chord.Chord_Diagram_for_1069 :Chord   [clone_a,clone_b]   (count)
   .Chord.Chord_Diagram_for_1070 :Chord   [clone_a,clone_b]   (count)
   .Chord.Chord_Diagram_for_1381 :Chord   [clone_a,clone_b]   (count)
   .Chord.Chord_Diagram_for_883  :Chord   [clone_a,clone_b]   (count)
   .Chord.Chord_Diagram_for_934  :Chord   [clone_a,clone_b]   (count)
   .Chord.Chord_Diagram_for_935  :Chord   [clone_a,clone_b]   (count)